In [1]:
import json
import dill  

from program import Program, ProgramWriter
from lm_poller import LMPoller
from text_preprocessing import extract_triplets, extract_relations
from lm_response_evaluator import extract_code, get_response_similarity, evaluate_response

with open('saved_trainer.pkl', 'rb') as f:
    trainer = dill.load(f)



/home/lango/personal_work_troja/software/miniconda3/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/lango/personal_work_troja/software/miniconda3/lib/python3.10/site-packages/transformers/utils/hub.py:124: FutureWarning: Using `TRANSFORMERS_CACHE` is deprecated and will be removed in v5 of Transformers. Use `HF_HOME` instead.
  warnings.warn(


In [2]:
print("---")
print(len(trainer.program.rules))
from evaluate_program import BERTScore, evaluate_program, get_basic_metrics
a,b = evaluate_program(trainer.program, get_basic_metrics())

---
3312


[nltk_data] Downloading package wordnet to /home/lango/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /home/lango/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/lango/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
/home/lango/personal_work_troja/software/miniconda3/lib/python3.10/site-packages/datasets/load.py:1486: FutureWarning: The repository for gem contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/gem
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this dataset from the next major release of `datasets`.
  warnings.warn(


The  J. R. R. Tolkien is a author by The Fellowship of the Ring, The novel The Silmarillion is a notable work by J. R. R. Tolkien,
METEOR: (array(0.1905293), array(0.20319508)) 
BLEU: (array(0.01282572), array(0.01522543), array(0.43984806), 0.5186020293122886) 


In [17]:
from evaluate_program import WebNLG
data = WebNLG()
data.load(['test'])

refs_single = []
preds_single = []
refs_multi = []
preds_multi = []
ref_lens = []
is_out_domain = []
for dataEntry in data.data:
    is_out_domain.append(dataEntry.category in ["Film", "MusicalWork", "Scientist"])

    relations = tuple(sorted([i.pred for i in dataEntry.data]))
    input = [tuple([triplet.subj, triplet.pred, triplet.obj]) for triplet in dataEntry.data]
    output = trainer.program.process_input(relations, dataEntry.data)
    print(f"{input}\n{output}\n\n")

/home/lango/personal_work_troja/software/miniconda3/lib/python3.10/site-packages/datasets/load.py:1486: FutureWarning: The repository for gem contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/gem
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this dataset from the next major release of `datasets`.
  warnings.warn(


[('Estádio Municipal Coaracy da Mata Fonseca', 'location', 'Arapiraca'), ('Agremiação Sportiva Arapiraquense', 'league', 'Campeonato Brasileiro Série C'), ('Campeonato Brasileiro Série C', 'country', 'Brazil'), ('Agremiação Sportiva Arapiraquense', 'nickname', 'Alvinegro'), ('Agremiação Sportiva Arapiraquense', 'ground', 'Estádio Municipal Coaracy da Mata Fonseca')]
SPLIT NEEDED


[('Nie Haisheng', 'birth date', '1964-10-13'), ('Nie Haisheng', 'occupation', 'Fighter pilot')]
SPLIT NEEDED


[('Motor sport Vision', 'city', 'Fawkham')]
Motor sport Vision is in the city of Fawkham.


[('Aleksandr Prudnikov', 'height', '185.0 (centimetres)'), ('FC Spartak Moscow', 'ground', 'Otkrytiye Arena'), ('Aleksandr Prudnikov', 'club', 'FC Spartak Moscow')]
SPLIT NEEDED


[('Ciudad Ayala', 'population metro', '1777539'), ('Ciudad Ayala', 'leader title', 'City Manager'), ('Ciudad Ayala', 'type', 'City'), ('Ciudad Ayala', 'population density', '1604.0'), ('Ciudad Ayala', 'government type', 'Council-mana

In [16]:
print(trainer.program.rules[('city',)].rule_code)
dataEntry=data.data[2]
relations = tuple(sorted([i.pred for i in dataEntry.data]))
input = [tuple([triplet.subj, triplet.pred, triplet.obj]) for triplet in dataEntry.data]
print(input)
trainer.program.process_input(relations, input)
relationset_str = tuple(sorted(relations))
trainer.program.rules[relationset_str].exec_rule(input)


    subj, _, obj = triplets[0]
    output = f"{subj} is in the city of {obj}."
    

[('Motor sport Vision', 'city', 'Fawkham')]


('', "'tuple' object has no attribute 'pred'")

In [3]:


#read json file from ../res/webnlg/train.json
with open('../res/webnlg/train.json', 'r', encoding='utf-8') as f:
    data = json.load(f)
    
# print(data['data'][0]['in'])
# print(len(data['data']))

data_dict = {}
for i in range(len(data['data'])):
    sample = data['data'][i]
    in_data = data['data'][i]['in']
    relations = extract_relations(in_data)
    relations = tuple(relations)

    if relations in data_dict:
        data_dict[relations].append(sample)
    else:
        data_dict[relations] = [sample]
        
keys = list(data_dict.keys())
example_id = -1
# print(f'{keys[example_id]}:\n {data_dict[keys[example_id]]}')


MAX_LLM_FIX_QUYERY = 5

from trainer import SimpleProgramTrainer, SimpleProgramLoader


trainer = SimpleProgramLoader()
trainer.train(data_dict)

print("---")
print(len(trainer.program.rules))
from evaluate_program import BERTScore, evaluate_program, get_basic_metrics
a,b = evaluate_program(trainer.program, get_basic_metrics())


Failed to generate rule for ('operating organisation',) after 1 attempts. Skipping...
Failed to generate rule for ('aircraft helicopter',) after 1 attempts. Skipping...
Failed to generate rule for ('division',) after 1 attempts. Skipping...
Failed to generate rule for ('alma mater',) after 1 attempts. Skipping...
Failed to generate rule for ('birth name',) after 1 attempts. Skipping...
Failed to generate rule for ('ribbon award',) after 1 attempts. Skipping...
Failed to generate rule for ('fossil',) after 1 attempts. Skipping...
Failed to generate rule for ('bird',) after 1 attempts. Skipping...
Failed to generate rule for ('coach',) after 1 attempts. Skipping...
Failed to generate rule for ('developer',) after 1 attempts. Skipping...
Failed to generate rule for ('added to the national register of historic places',) after 1 attempts. Skipping...
Failed to generate rule for ('epoch',) after 1 attempts. Skipping...
Failed to generate rule for ('discovered',) after 1 attempts. Skipping...

Errors: None
similarity: 0.8461538461538461
output: The Aarhus Airport is the airport of AarhusDenmark, Denmark
reference: The Aarhus is the airport of Aarhus, Denmark.


Errors: None
similarity: 0.9777777777777777
output: Aarhus Airport is 25.0 metres above sea level.
reference: Aarhus Airport is 25 metres above sea level.


Errors: None
similarity: 0.935064935064935
output: Aarhus Airport is location in Tirstrup.
reference: Aarhus Airport is located in Tirstrup.


Errors: None
similarity: 0.0
output: 
reference: Aarhus Airport is operated by Aarhus Lufthavn A/S.


Errors: None
similarity: 1.0
output: Aarhus Airport runway length is 2776.0.
reference: Aarhus Airport runway length is 2776.0.


Errors: None
similarity: 1.0
output: Aarhus Airport runway name is 10L/28R.
reference: Aarhus Airport runway name is 10L/28R.


Errors: None
similarity: 1.0
output: Abilene, Texas is in the United States.
reference: Abilene, Texas is in the United States.


Errors: None
similarity: 0.989010989010

Failed to generate rule for ('last aired',) after 1 attempts. Skipping...
Failed to generate rule for ('maiden voyage',) after 1 attempts. Skipping...
Failed to generate rule for ('failed launches',) after 1 attempts. Skipping...
Failed to generate rule for ('comparable',) after 1 attempts. Skipping...
Failed to generate rule for ('final flight',) after 1 attempts. Skipping...
Failed to generate rule for ('municipality',) after 1 attempts. Skipping...
Failed to generate rule for ('dedicated to',) after 1 attempts. Skipping...
Failed to generate rule for ('has deputy',) after 1 attempts. Skipping...
Failed to generate rule for ('in office while president',) after 1 attempts. Skipping...
Failed to generate rule for ('place',) after 1 attempts. Skipping...
Failed to generate rule for ('preceded by',) after 1 attempts. Skipping...
Failed to generate rule for ('editor',) after 1 attempts. Skipping...
Failed to generate rule for ('libraryof congress classification',) after 1 attempts. Skippi

Errors: None
similarity: 0.9915966386554622
output: The creator of Airman (comics character) is George Kapitan.
reference: The creator of Airman, (comics character) is George Kapitan.


Errors: None
similarity: 1.0
output: The full name of Auron (comics character) is "Lambien".
reference: The full name of Auron (comics character) is "Lambien".


Errors: None
similarity: 0.989247311827957
output: BBC was founded by John Reith, 1st Baron Reith.
reference: BBC was founded by John Reith 1st Baron Reith.


Errors: None
similarity: 1.0
output: Rona Fairhead is the key person for BBC.
reference: Rona Fairhead is the key person for BBC.


Errors: None
similarity: 0.975
output: One of the products of BBC is BBC Radio.
reference: One of the products of BBC is BBC radio.


Errors: name 'month_dict' is not defined
similarity: 0.0
output: 
reference: Bananaman last aired on April 15th 1986.


Errors: None
similarity: 1.0
output: Graeme Garden stars in Bananaman.
reference: Graeme Garden stars in Ba

Failed to generate rule for ('city served', 'is part of') after 1 attempts. Skipping...
Failed to generate rule for ('location identifier', 'elevation above the sea level') after 1 attempts. Skipping...
Failed to generate rule for ('leader', 'location') after 1 attempts. Skipping...
Failed to generate rule for ('city served', 'runway length') after 1 attempts. Skipping...
Failed to generate rule for ('battle', 'operating organisation') after 1 attempts. Skipping...
Failed to generate rule for ('city served', 'capital') after 1 attempts. Skipping...
Failed to generate rule for ('location', 'leader title') after 1 attempts. Skipping...
Failed to generate rule for ('1st runway number', 'elevation above the sea level') after 1 attempts. Skipping...
Failed to generate rule for ('4th runway surface type', 'elevation above the sea level') after 1 attempts. Skipping...
Failed to generate rule for ('5th runway surface type', 'elevation above the sea level') after 1 attempts. Skipping...
Failed 

...

Errors: None
similarity: 0.005376344086021506
output: The company None were the architects of the 3Arena at None. The arena, which has a height of None, was completed in None and hosts None.
reference: Elliot See attended the University of Texas in Austin (affiliated to the university of Texas system). He died in St. Louis. The president of the University of Texas is Gregory L. Fenves. The name of St. Louis' leader is Francis G. Slay.


Errors: None
similarity: 0.2964824120603015
output: Elliot See alma mater University of Texas at Austin death place St. Louis death date 1966-02-28. University of Texas at Austin affiliation University of Texas System compete in Big 12 Conference. 
reference: Elliot See attended the University of Texas at Austin, which is affiliated to the University of Texas System and will compete in the Big 12 Conference. Elliot See died in St. Louis on February 28, 1966.


Errors: None
similarity: 0.657074340527578
output: Elliot See is alma mater University of Texa

Failed to generate rule for ('orbital period', 'former name', 'epoch', 'periapsis', 'escape velocity') after 1 attempts. Skipping...
Failed to generate rule for ('orbital period', 'epoch', 'apoapsis', 'mean temperature', 'periapsis') after 1 attempts. Skipping...
Failed to generate rule for ('orbital period', 'epoch', 'apoapsis', 'periapsis', 'escape velocity') after 1 attempts. Skipping...
Failed to generate rule for ('orbital period', 'epoch', 'density', 'periapsis', 'escape velocity') after 1 attempts. Skipping...


Errors: name 'triplets' is not defined
similarity: 0.0
output: 
reference: (66063) 1998 RO1-former name "1999 SN5"- has an orbital period of 360.29 days and its epoch date was on 13th January 2016.Its periapsis is 41498400000.0 Gm and it has an escape velocity of 0.0999 km/s.


Errors: None
similarity: 0.0
output: 
reference: (66063) 1998 RO1, which has the epoch date of 4 November 2013, has a mean temperature of 265 kelvins and an orbital period of 360.29 days. The asteroid has a periapsis measurement of 41498400000.0 and an apoapsis of 254989570.60815 kilometres.


Errors: list index out of range
similarity: 0.0
output: 
reference: (66063) 1998 RO1 which has an orbital period of 360.29 days and an escape velocity of 0.0999 km per sec, has the epoch date of 4 November 2013. The asteroid has a periapsis of 41498400000.0 and apoapsis of 254989570.60815 kilometres.


Errors: None
similarity: 0.31007751937984496
output: (66391) 1999 KW4, epoch the 0 escape velocity the 16244700.0 orbital 

/home/lango/personal_work_troja/software/miniconda3/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/lango/personal_work_troja/software/miniconda3/lib/python3.10/site-packages/transformers/utils/hub.py:124: FutureWarning: Using `TRANSFORMERS_CACHE` is deprecated and will be removed in v5 of Transformers. Use `HF_HOME` instead.
  warnings.warn(
[nltk_data] Downloading package wordnet to /home/lango/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /home/lango/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/lango/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
/home/lango/personal_work_troja/software/miniconda3/lib/python3.10/site-packages/datasets/load.py:1486: 

The J. R. R. Tolkien of The Fellowship of the Ring is author, . The The Silmarillion of J. R. R. Tolkien is notable work, .
METEOR: (array(0.13539139), array(0.13097865)) 
BLEU: (array(0.0026052), array(0.00157273), array(0.44159295)) 


In [1]:
response = '''Here is a sample for the data-to-text dataset:

#### Sample
in: (Albert Einstein, leader, None), (Albert Einstein, alma mater, Swiss Federal Polytechnic University), (Swiss Federal Polytechnic University, location, Zurich)
out: Albert Einstein was a leader who studied at Swiss Federal Polytechnic University located in Zurich.'''

In [6]:

class ResponsesHandler:
    def __init__(self, logger=None):
        self.logger = logger

    def extract_sample(self, response, relations) -> dict[str, str] | None:
        raise NotImplementedError

    def _extract_from_tags(self, response, start_tag="<sample>", end_tag="</sample>"):
        try:
            sample = response.strip().split(start_tag)[-1].split(end_tag)[0]
            return sample

        except Exception as e:
            self.logger.error(f'Failed to extract sample from response: {response} due to {e}') if self.logger else None
            return None


class StringResponseHandler(ResponsesHandler):
    def __init__(self, logger=None):
        super().__init__(logger)

    def extract_sample(self, response, relations) -> dict[str, str] | None:
        sample = self._extract_from_tags(response)
        triples = sample.split('in: ')[-1].split('out: ')[0].strip()
        output = sample.split("out: ")[-1].strip()

        return {
            'in': triples,
            'out': output,
        }

h = StringResponseHandler()
h.extract_sample(response, "")


{'in': '(Albert Einstein, leader, None), (Albert Einstein, alma mater, Swiss Federal Polytechnic University), (Swiss Federal Polytechnic University, location, Zurich)',
 'out': 'Albert Einstein was a leader who studied at Swiss Federal Polytechnic University located in Zurich.'}

In [43]:
# len([(i,j) for i,j in zip(a,b) if i not in ( "OUT OF DOMAIN")])
from evaluate_program import WebNLG
data = WebNLG()
data.load(['train'])

/home/lango/personal_work_troja/software/miniconda3/lib/python3.10/site-packages/datasets/load.py:1486: FutureWarning: The repository for gem contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/gem
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this dataset from the next major release of `datasets`.
  warnings.warn(


[{'data': [RDFTriple(subj='Alderney', pred='capital', obj='Saint Anne, Alderney')], 'refs': ['Saint Anne is the capital of Alderney.'], 'data_type': 'triples', 'align': None, 'num_ref_sentences': None, 'category': 'Airport', 'dialhist': None, 'entry_id': 'train_Airport_1_Id76'}, {'data': [RDFTriple(subj='Alderney', pred='language', obj='English language')], 'refs': ['The main language spoken on Alderney is English.'], 'data_type': 'triples', 'align': None, 'num_ref_sentences': None, 'category': 'Airport', 'dialhist': None, 'entry_id': 'train_Airport_1_Id77'}, {'data': [RDFTriple(subj='Alderney', pred='language', obj='English language')], 'refs': ['The English language is spoken in Alderney.'], 'data_type': 'triples', 'align': None, 'num_ref_sentences': None, 'category': 'Airport', 'dialhist': None, 'entry_id': 'train_Airport_1_Id77'}, {'data': [RDFTriple(subj='Alderney', pred='language', obj='English language')], 'refs': ['Alderney uses the English language.'], 'data_type': 'triples', 

In [40]:

class ExampleFinder:
    def __init__(self, data):
        from evaluate_program import WebNLG
        data = WebNLG()
        data.load(['train'])

    def find_similar_examples(self, relations):
        relations = set(relations)
        filtered = [d for d in self.data.data if relations  &  set([i.pred for i in d.data]) ]
        result = [] 
        while len(relations) != 0:
            best = None
            best_val = 0
            for f in filtered:
                size_of_intersection = len(relations  &  set([i.pred for i in f.data]) )
                if size_of_intersection > best_val:
                    best = f
                    best_val = size_of_intersection
                elif size_of_intersection == best_val:
                    if len(f.data) < len(best.data):
                        best = f
            if best is None:
                break
            result.append(best)
            covered_relations = set([i.pred for i in best.data])
            relations = set([r for r in relations if r not in covered_relations])
        
        return result
    
    def is_complete(self, list_of_examples, relations):
        relation_in_set = set([item.pred for example in list_of_examples for item in example.data])
        return relations.issubset(relation_in_set)
    
    def recursive(self, list_of_examples, filtered, min_joints_found, relations):
        rel = set([item.pred for example in list_of_examples for item in example.data])
        possible_joins = [d for d in filtered if not set([i.pred for i in d.data]).issubset(rel) ]
        print(f"Call {min_joints_found}, {len(possible_joins)}: {rel}")
        triplets_set = set([item for example in list_of_examples for item in example.data])
        possible_joins = [d for d in possible_joins if triplets_set & set(d.data) and d not in list_of_examples ]
        print(f"Call {min_joints_found}, {len(possible_joins)}: {rel}")
        possible_joins = sorted(possible_joins, key=lambda x: len(set(x.data) - triplets_set), reverse=True)
        # czy wyczerpuje relacje? w ile joinów
        best_solution = None
        for x in possible_joins:
            new_list_of_examples = [x] + list_of_examples
            rel = set([item.pred for example in new_list_of_examples for item in example.data])
            print(f"New {rel}")
            if self.is_complete(new_list_of_examples,relations): 
                print("Complete")
                return new_list_of_examples  # bo i tak każde inne jest dłuższe o 1
            else:
                if len(new_list_of_examples) +1 < min_joints_found:
                    solution = self.recursive(new_list_of_examples, possible_joins, min_joints_found, relations)
                    if solution is not None:
                        min_joints_found = len(solution)
                        best_solution = solution
        return best_solution

    
    def find_set_of_triples(self,relations):
        """
        Zwróć najkrótszą listę trójek, które
         - zawierają tylko potrzebne relacje
         - wartości trójek się przecinają
         - odpowiadające teksty referencyjne są błędne
        """
        #filtruj dane ktore nie maja porządanych relacji
        filtered = [d for d in self.data.data if relations  &  set([i.pred for i in d.data]) ]
        for d in filtered:
            rel_in_d = [i for i in d.data if i.pred not in relations]
            for x in rel_in_d:
                d.data.remove(x)
                
        filtered = sorted(filtered, key=lambda x: len(x.data), reverse=True)
        best_solution = None
        min_joints_found = 10
        for x in filtered:
            solution = self.recursive([x], filtered, min_joints_found, relations)
            if solution is None:
                continue
            if len(solution) < min_joints_found:
                print("SOL+++++++++++++++++++++++++++++")
                min_joints_found = len(solution)
                best_solution = solution
            if min_joints_found == 2:
                break
        return best_solution, min_joints_found

    def find_set_of_examples(self,relations):
        """
        Zwróć najkrótszą listę przykładów, które
         - zawierają tylko potrzebne relacje
         - zawierają odpowiednie teksty referencyjne
         - wartości trójek się przecinają
        """
        #filtruj dane ktore nie maja porządanych relacji
        # filtered = [d for d in self.data.data if relations  &  set([i.pred for i in d.data]) ]
        filtered = [d for d in self.data.data if  set([i.pred for i in d.data]).issubset(relations) ]
        #posrtuj znalezione dane od największego do najmniejszego przecięcia ze zbiorem relacji
        # filtered = sorted(filtered, key=lambda x: len(relations  &  set([i.pred for i in x.data]) ), reverse=True)
        filtered = sorted(filtered, key=lambda x: len(x.data), reverse=True)
        best_solution = None
        min_joints_found = 10
        for x in filtered:
            solution = self.recursive([x], filtered, min_joints_found, relations)
            if solution is None:
                continue
            if len(solution) < min_joints_found:
                print("SOL+++++++++++++++++++++++++++++")
                min_joints_found = len(solution)
                best_solution = solution
            if min_joints_found == 2:
                break
        return best_solution, min_joints_found

        #iteruj szukając przykładu który ma przecięcie z trójkami aktualnego + sprawdż czy brakujące relacje można uzupełnić
relations = set("last aired;broadcasted by;city;creator".split(";"))
print("DF")
ef = ExampleFinder(data)
out  = ef.find_similar_examples(relations)
print("DF")
print(out)



DF
DF
[{'data': [RDFTriple(subj='Bananaman', pred='broadcasted by', obj='BBC'), RDFTriple(subj='Bananaman', pred='creator', obj='John Geering'), RDFTriple(subj='Bananaman', pred='last aired', obj='1986-04-15')], 'refs': ['Bananaman first aired on the BBC on October 3rd, 1983 and broadcast its last episode on April 15th, 1986. Bananaman last aired on 15th April 1986. Graeme Garden is one of the stars of the series which was created by John Geering.'], 'data_type': 'triples', 'align': None, 'num_ref_sentences': None, 'category': 'ComicsCharacter', 'dialhist': None, 'entry_id': 'train_ComicsCharacter_5_Id1'}, {'data': [RDFTriple(subj='ENAIRE', pred='city', obj='Madrid')], 'refs': ['ENAIRE is in the city of Madrid.'], 'data_type': 'triples', 'align': None, 'num_ref_sentences': None, 'category': 'Airport', 'dialhist': None, 'entry_id': 'train_Airport_1_Id215'}]


In [42]:
out[1].data

[RDFTriple(subj='ENAIRE', pred='city', obj='Madrid')]